# Datasets

### Estrazione dataset MC

In [133]:
import pandas as pd
import os
from pathlib import Path

def carica_training_dataset():
    """
    Cerca il file Training_datasetMC.csv nelle cartelle tipiche del progetto,
    lo carica, lo pulisce e restituisce un DataFrame con colonne:
    - text
    - label (0/1)
    """

    # 1) Capisco da dove sto eseguendo il notebook
    cwd = Path().resolve()
    print("Current working dir:", cwd)

    # 2) Elenco di possibili percorsi dove potrebbe stare il CSV
    candidate_paths = [
        cwd / "Training_datasetMC.csv",
        cwd / "DataRaw" / "Training_datasetMC.csv",
        cwd.parent / "DataRaw" / "Training_datasetMC.csv",
        cwd.parent / "src" / "DataRaw" / "Training_datasetMC.csv",
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            "Non trovo Training_datasetMC.csv. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico:", path_input)

    # 3) Lettura robusta del CSV (gestisce le virgole dentro le frasi)
    df = pd.read_csv(
        path_input,
        header=None,
        names=["id", "text", "label"],
        quotechar='"',
        sep=",",
        encoding="utf-8",
        engine="python",    # parser più tollerante
        on_bad_lines="skip" # salta eventuali righe rovinate
    )

    print("Shape originale:", df.shape)

    # 4) Rimuovo la colonna ID
    df = df.drop(columns=["id"])

    # 5) Pulizia base del testo
    df["text"] = (
        df["text"]
        .astype(str)
        .str.strip()
        .str.replace(r'^"|"$', "", regex=True)  # rimuove doppi apici ai bordi se presenti
    )

    # 6) Pulizia e conversione della label
    df["label"] = pd.to_numeric(df["label"], errors="coerce")
    df = df.dropna(subset=["label"])
    df["label"] = df["label"].astype(int)

    # 7) Tolgo eventuali righe con testo vuoto
    df = df[df["text"].str.len() > 0]

    # 8) Tolgo eventuali duplicati
    df = df.drop_duplicates(subset=["text", "label"])

    print("Shape pulito:", df.shape)
    return df

train_dfMC = carica_training_dataset()


Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\Training_datasetMC.csv
Shape originale: (3996, 3)
Shape pulito: (3995, 2)


In [134]:
# Opzioni estetiche per vedere meglio le frasi
pd.set_option("display.max_colwidth", 200)
pd.set_option("display.max_rows", 40)

train_dfMC = carica_training_dataset()

# Distribuzione ironia / non ironia
print(train_dfMC["label"].value_counts())



Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\Training_datasetMC.csv
Shape originale: (3996, 3)
Shape pulito: (3995, 2)
label
0    2006
1    1989
Name: count, dtype: int64


In [135]:

from IPython.display import display, HTML

html_table = train_dfMC.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))


Abbiamo un numero molto vicino tra le 2 classi
Non avremo problemi di ...

### Pulizia del dataset

Mescolo gli elementi del dataset, per avere omogeneità

In [136]:
# Mescolo completamente le righe del dataset
train_dfMC_shuffled = (
    train_dfMC
    .sample(frac=1, random_state=43)  # frac=1 => prende il 100% delle righe in ordine casuale
    .reset_index(drop=True)           # resetta l'indice dopo lo shuffle
)

train_dfMC = train_dfMC_shuffled

In [137]:
from IPython.display import display, HTML

html_table = train_dfMC_shuffled.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))


**Non verrà rimossa la punteggiatura**  
Il modello transformer tratta come token unici anche gli elementi di punteggiatura, utili per capire l'ironia.

**Però rimuoveremo le EMOJI**  = Sono poche, quindi non porterebbero informazione al nostro modello

**Trasformeremo tutto in minuscolo**  = E' standard per questo tipo di modelli testuali

**Uniformare gli apostrofi**  =  ' unico tipo apostrofo, più facile da tokenizzare

**Rimuovere spazi multipli** = usati per la tokenizzazione



In [138]:
import re


# Regex UNIVERSALE che prende (quasi) tutte le emoji moderne:
emoji_pattern = re.compile(
    "["
    "\U0001F000-\U0001FFFF"  # tutto il blocco multilingue (contiene TUTTE le emoji moderne)
    "\u2600-\u26FF"          # simboli vari (☀️, ☂️ ecc.)
    "\u2700-\u27BF"          # dingbats (✂️, ✌️ ecc.)
    "]+",
    flags=re.UNICODE
)


def pulisci_testo(t):
    t = str(t)

    # 1. rimozione emoji
    t = emoji_pattern.sub(r'', t)

    # 2. minuscolo
    t = t.lower()

    # 3. normalizzazione apostrofi
    t = t.replace("’", "'").replace("‘", "'")

    # 4. rimuove spazi multipli
    t = re.sub(r"\s+", " ", t)

    # 5. rimuove spazi ai bordi
    t = t.strip()

    return t

train_dfMC["text"] = train_dfMC["text"].apply(pulisci_testo)


In [139]:
from IPython.display import display, HTML

html_table = train_dfMC.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))

### Estrazione dataset IronITA

Estraiamo il training set di IronITA, rimuoviamo le colonne che non ci interessano e unifichiamo **Irony** e **Sarcasm**,
- se c'è 1 in almeno uno dei due, allora => 1
- se non c'è allora => 0

In [140]:
import pandas as pd
from pathlib import Path

def carica_training_ironita():
    """
    Carica il file training_ironita2018.xlsx, elimina id e topic,
    unisce irony e sarcasm in un'unica label binaria (0/1) e
    restituisce un DataFrame con colonne:
      - text
      - label (1 se ironia o sarcasmo, 0 altrimenti)
    """

    cwd = Path().resolve()
    print("Current working dir:", cwd)

    filename = "training_ironita2018.xlsx"

    # Possibili percorsi (come per MC)
    candidate_paths = [
        cwd / filename,
        cwd / "DataRaw" / filename,
        cwd.parent / "DataRaw" / filename,
        cwd.parent / "src" / "DataRaw" / filename,
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            f"Non trovo {filename}. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print("Carico:", path_input)

    # Leggo l'Excel (header sulla prima riga)
    df = pd.read_excel(path_input)

    print("Colonne trovate:", list(df.columns))
    print("Shape originale:", df.shape)

    # Normalizzo i nomi delle colonne (minuscolo, niente spazi)
    df.columns = [c.strip().lower() for c in df.columns]

    # Mi aspetto queste colonne: id, text, irony, sarcasm, topic
    # In caso di nomi leggermente diversi puoi sistemarli qui.
    text_col = "text"
    irony_col = "irony"
    sarcasm_col = "sarcasm"

    # Riempio eventuali NaN con 0 nelle colonne irony/sarcasm
    df[irony_col] = df[irony_col].fillna(0)
    df[sarcasm_col] = df[sarcasm_col].fillna(0)

    # Converto a intero (0/1)
    df[irony_col] = df[irony_col].astype(int)
    df[sarcasm_col] = df[sarcasm_col].astype(int)

    # Nuova label: 1 se almeno uno dei due è 1, altrimenti 0
    df["label"] = ((df[irony_col] == 1) | (df[sarcasm_col] == 1)).astype(int)

    # Costruisco il DataFrame finale: SOLO text + label
    df_out = df[[text_col, "label"]].copy()

    # Tolgo eventuali righe vuote / NaN nel testo
    df_out = df_out.dropna(subset=["text"])
    df_out["text"] = df_out["text"].astype(str).str.strip()
    df_out = df_out[df_out["text"].str.len() > 0]

    # Tolgo duplicati testo+label (facoltativo ma pulito)
    df_out = df_out.drop_duplicates(subset=["text", "label"])

    print("Shape pulito IronITA train:", df_out.shape)
    print("Distribuzione label:")
    print(df_out["label"].value_counts())

    return df_out


In [141]:
train_dfITA = carica_training_ironita()
from IPython.display import display, HTML

html_table = train_dfITA.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))


Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\training_ironita2018.xlsx
Colonne trovate: ['id', 'text', 'irony', 'sarcasm', 'topic']
Shape originale: (3977, 5)
Shape pulito IronITA train: (3976, 2)
Distribuzione label:
label
1    2022
0    1954
Name: count, dtype: int64


### Pulizia del dataset

Mescolo gli elementi del dataset, per avere omogeneità

In [142]:
def mescola_dataset(df, seed=42):
    """
    Restituisce un nuovo DataFrame mescolato completamente.
    seed: per garantire la riproducibilità
    """
    df_shuffled = df.sample(frac=1, random_state=seed).reset_index(drop=True)
    return df_shuffled
train_dfITA = mescola_dataset(train_dfITA)

In [143]:
from IPython.display import display, HTML

html_table = train_dfITA.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))

**Non verrà rimossa la punteggiatura**  
Il modello transformer tratta come token unici anche gli elementi di punteggiatura, utili per capire l'ironia.

**Però rimuoveremo le EMOJI**  = Sono poche, quindi non porterebbero informazione al nostro modello

**Trasformeremo tutto in minuscolo**  = E' standard per questo tipo di modelli testuali

**Uniformare gli apostrofi**  =  ' unico tipo apostrofo, più facile da tokenizzare

**Rimuovere spazi multipli** = usati per la tokenizzazione

**sostituire @nome con account** = non avrò mille token diversi per ogni nome

**tolgo # ma mantengo la parola** = spesso è una parola chiave nella frase, non voglio perderla del tutto

**Tolgo i link http** = non portano semantica

**Tolgo []** = sarebbero token inutili

**Tolgo date** = non portano ironia (nella maggior parte delle volte)

In [144]:
import re
import html

# Regex UNIVERSALE che prende (quasi) tutte le emoji moderne:
emoji_pattern = re.compile(
    "["
    "\U0001F000-\U0001FFFF"  # tutto il blocco multilingue (contiene TUTTE le emoji moderne)
    "\u2600-\u26FF"          # simboli vari (☀️, ☂️ ecc.)
    "\u2700-\u27BF"          # dingbats (✂️, ✌️ ecc.)
    "]+",
    flags=re.UNICODE
)


def pulisci_tweet_ironita(t: str) -> str:
    t = str(t)

    # 1) Rimuovo i link (http..., https..., www...)
    t = re.sub(r"http\S+|www\.\S+", " ", t)

    # 2) Sostituisco @username con token generico "account"
    t = re.sub(r"@\w+", " account ", t)

    # 3) Tolgo le parentesi quadre [ ]
    t = t.replace("[", " ").replace("]", " ")

    # 4) Rimuovo emoji
    t = emoji_pattern.sub("", t)

    # 5) Tolgo il simbolo # ma tengo la parola del tag
    #    es. "#labuonascuola" -> "labuonascuola"
    t = re.sub(r"#(\w+)", r"\1", t)

    # 6) Minuscolo + normalizzazione apostrofi
    t = t.lower()
    t = t.replace("’", "'").replace("‘", "'")

    # 7) Comprimo spazi multipli e strip finale
    t = re.sub(r"\s+", " ", t)
    t = t.strip()

    # 8) rimuovo date tipo 19/01/2012
    t = re.sub(r"\b\d{1,2}/\d{1,2}/\d{2,4}\b", " ", t)

    # 9) separa numeri e lettere attaccati: 5figli → 5 figli
    t = re.sub(r"(\d)([a-zàèéìòù])", r"\1 \2", t, flags=re.IGNORECASE)
    t = re.sub(r"([a-zàèéìòù])(\d)", r"\1 \2", t, flags=re.IGNORECASE)

    # 0) Decodifica gli artefatti HTML (&gt; -> >, &amp; -> &, ... )
    t = html.unescape(t)

    # 1) Rimuove simboli di markup tipo < > / 
    t = re.sub(r"[<>/]", " ", t)

    # 2) Rimuove frecce, sequenze di trattini, ----->, --->, --- ecc.
    t = re.sub(r"-{2,}|\>{2,}", " ", t)

    # 3) Comprimi eventuali spazi dopo la pulizia
    t = re.sub(r"\s+", " ", t)

    # Rimuove trattini singoli e backslash
    t = re.sub(r"[-\\]", " ", t)

    # Rimuove caratteri non validi / replacement character (�)
    t = t.replace("�", "")



    return t

train_dfITA["text"] = train_dfITA["text"].apply(pulisci_tweet_ironita)

In [145]:
from IPython.display import display, HTML

html_table = train_dfITA.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))

### Creazione del Test set

In [148]:
import pandas as pd
from pathlib import Path
import re
import html

# ==========================
#  Emoji: regex "universale"
# ==========================
emoji_pattern = re.compile(
    "["                       # intervalli che coprono praticamente tutte le emoji moderne
    "\U0001F000-\U0001FFFF"   # simboli/emoji multilingue
    "\u2600-\u26FF"           # simboli vari (☀️, ☂️, ♥, ecc.)
    "\u2700-\u27BF"           # dingbats (✂️, ✌️, ecc.)
    "]+",
    flags=re.UNICODE
)

# ================================
#  Funzione generica di caricamento
#  per IronyITA (train / test)
# ================================
def carica_ironita(split="train"):
    """
    Carica il file IronyITA (training_ironita2018.xlsx o test_ironita2018.xlsx),
    elimina id e topic, unisce irony e sarcasm in un'unica label binaria (0/1)
    e restituisce un DataFrame con colonne:
      - text
      - label (1 se ironia o sarcasmo, 0 altrimenti)
    split: "train" oppure "test"
    """

    cwd = Path().resolve()
    print("Current working dir:", cwd)

    filename = "training_ironita2018.xlsx" if split == "train" else "test_ironita2018.xlsx"

    candidate_paths = [
        cwd / filename,
        cwd / "DataRaw" / filename,
        cwd.parent / "DataRaw" / filename,
        cwd.parent / "src" / "DataRaw" / filename,
    ]

    path_input = None
    for p in candidate_paths:
        if p.exists():
            path_input = p
            break

    if path_input is None:
        raise FileNotFoundError(
            f"Non trovo {filename}. Ho provato questi percorsi:\n" +
            "\n".join(str(p) for p in candidate_paths)
        )

    print(f"Carico {split} da:", path_input)

    # Leggo l'Excel (header sulla prima riga)
    df = pd.read_excel(path_input)
    print("Colonne trovate:", list(df.columns))
    print("Shape originale:", df.shape)

    # Normalizzo i nomi delle colonne (minuscolo, niente spazi)
    df.columns = [c.strip().lower() for c in df.columns]

    # Mi aspetto: id, text, irony, sarcasm, topic
    text_col    = "text"
    irony_col   = "irony"
    sarcasm_col = "sarcasm"

    # Riempio eventuali NaN con 0 nelle colonne irony/sarcasm
    df[irony_col]   = df[irony_col].fillna(0)
    df[sarcasm_col] = df[sarcasm_col].fillna(0)

    # Converto a intero (0/1)
    df[irony_col]   = df[irony_col].astype(int)
    df[sarcasm_col] = df[sarcasm_col].astype(int)

    # Nuova label: 1 se almeno uno dei due è 1, altrimenti 0
    df["label"] = ((df[irony_col] == 1) | (df[sarcasm_col] == 1)).astype(int)

    # DataFrame finale: SOLO text + label
    df_out = df[[text_col, "label"]].copy()

    # Tolgo eventuali righe vuote / NaN nel testo
    df_out = df_out.dropna(subset=["text"])
    df_out["text"] = df_out["text"].astype(str).str.strip()
    df_out = df_out[df_out["text"].str.len() > 0]

    # Tolgo duplicati testo+label (facoltativo ma pulito)
    df_out = df_out.drop_duplicates(subset=["text", "label"])

    print(f"Shape pulito IronITA {split}:", df_out.shape)
    print("Distribuzione label:")
    print(df_out["label"].value_counts())

    return df_out

# ==========================
#  Mescola dataset
# ==========================
def mescola_dataset(df, seed=42):
    """
    Restituisce un nuovo DataFrame mescolato completamente.
    seed: per garantire la riproducibilità
    """
    return df.sample(frac=1, random_state=seed).reset_index(drop=True)

# ==========================
#  Pulizia testo IronyITA
# ==========================
def pulisci_tweet_ironita(t: str) -> str:
    t = str(t)

    # 0) Decodifica artefatti HTML (&gt; -> >, &amp; -> &, ecc.)
    t = html.unescape(t)

    # 1) Rimuovo i link (http..., https..., www...)
    t = re.sub(r"http\S+|www\.\S+", " ", t)

    # 2) Sostituisco @username con token generico "account"
    t = re.sub(r"@\w+", " account ", t)

    # 3) Tolgo le parentesi quadre [ ]
    t = t.replace("[", " ").replace("]", " ")

    # 4) Rimuovo emoji
    t = emoji_pattern.sub("", t)

    # 5) Tolgo il simbolo # ma tengo la parola del tag (#labuonascuola -> labuonascuola)
    t = re.sub(r"#(\w+)", r"\1", t)

    # 6) Rimuovo date tipo 19/01/2012
    t = re.sub(r"\b\d{1,2}/\d{1,2}/\d{2,4}\b", " ", t)

    # 7) Rimuove simboli di markup tipo < > / (nel caso ce ne siano ancora)
    t = re.sub(r"[<>/]", " ", t)

    # 8) Rimuove frecce e sequenze di trattini (----->, --->, ---)
    t = re.sub(r"-{2,}|\>{2,}", " ", t)

    # 9) Rimuove trattini singoli e backslash
    t = re.sub(r"[-\\]", " ", t)

    # 10) Rimuove caratteri non validi / replacement character (�)
    t = t.replace("�", " ")

    # 11) Minuscolo + normalizzazione apostrofi
    t = t.lower()
    t = t.replace("’", "'").replace("‘", "'")

    # 12) Separa numeri e lettere attaccati: 5figli → 5 figli
    t = re.sub(r"(\d)([a-zàèéìòù])", r"\1 \2", t, flags=re.IGNORECASE)
    t = re.sub(r"([a-zàèéìòù])(\d)", r"\1 \2", t, flags=re.IGNORECASE)

    # 13) Comprimo spazi multipli e strip finale
    t = re.sub(r"\s+", " ", t).strip()

    return t

# ==========================
#  Carico, mescolo, pulisco
# ==========================

# TRAIN IronyITA
train_dfITA = carica_ironita(split="train")
train_dfITA = mescola_dataset(train_dfITA)
train_dfITA["text"] = train_dfITA["text"].apply(pulisci_tweet_ironita)

# TEST IronyITA
test_dfITA = carica_ironita(split="test")
test_dfITA = mescola_dataset(test_dfITA)
test_dfITA["text"] = test_dfITA["text"].apply(pulisci_tweet_ironita)

print("\nEsempi TRAIN puliti:")
print(train_dfITA.head(5))

print("\nEsempi TEST puliti:")
print(test_dfITA.head(5))


Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico train da: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\training_ironita2018.xlsx
Colonne trovate: ['id', 'text', 'irony', 'sarcasm', 'topic']
Shape originale: (3977, 5)
Shape pulito IronITA train: (3976, 2)
Distribuzione label:
label
1    2022
0    1954
Name: count, dtype: int64
Current working dir: C:\Users\marco\Desktop\IronyDetection\src\Code
Carico test da: C:\Users\marco\Desktop\IronyDetection\src\DataRaw\test_ironita2018.xlsx
Colonne trovate: ['id', 'text', 'topic']
Shape originale: (872, 3)


KeyError: 'irony'

# I Dataset

### IronITA

In [146]:

from IPython.display import display, HTML

html_tableA = train_dfITA.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_tableA}
</div>
"""))

### MC

In [147]:
from IPython.display import display, HTML

html_table = train_dfMC.to_html(max_rows=None)

display(HTML(f"""
<div style="height:300px; overflow-y: scroll; border:1px solid #ccc;">
{html_table}
</div>
"""))

Quindi il avremo 2 dataset : 
- IronITA = estratto da twitter nel 2018, rimane ancora un po sporco, dato che proviene da chat social reali   
(errori di battitura, parole inventate, parole unite, artefatti ... => saranno **token rari** ci penserà il transformer a darci meno peso a queste)

- MC = prodotto da me, è più pulito in quanto le frasi sono state scritte ed etichettate a mano

**Entrambi i dataset avranno circa 2000 frasi ironiche e 2000 frasi non ironiche**

Quindi avremmo 2 dataset, con ironia diversa, stile di scrittura diversa ecc...  
Potremmo :
- Addestrare il modello solo con MC
- Addestrare il modello solo con IronITA
- Mescolarli (più dati) e addestrarli con entrambi

e vedere quale modello avrà un efficienza maggiore...

### Test set

Di conseguenza crerò anche 3 test set, da 1000 frasi l'uno,  
 che potranno poi essere alternati su ogni modello e verificare l'efficienza di ognuno e vedere se cambia di tanto